The scripts in this notebook are rather disjointed and untidy. This is because it was run on the AWS cloud and was complicated by long processing times and the 4hr timer resetting. This required multiple get and post requests to the project S3 bucket.

# Installing and importing packages

In [19]:
!pip install awswrangler

Looking in indexes: https://pypi.org/simple, https://pip.repos.neuron.amazonaws.com


In [20]:
import awswrangler as wr

In [21]:
wr.s3.list_objects("s3://dsp-data-vq22301")

['s3://dsp-data-vq22301/all_data.csv',
 's3://dsp-data-vq22301/all_data_pc_merged.csv',
 's3://dsp-data-vq22301/dataset_0-7575.csv',
 's3://dsp-data-vq22301/dataset_16294-end.csv',
 's3://dsp-data-vq22301/dataset_7576-16293.csv',
 's3://dsp-data-vq22301/dataset_drop_md.csv',
 's3://dsp-data-vq22301/final_dataset.csv',
 's3://dsp-data-vq22301/final_dataset_drop_target_na.csv',
 's3://dsp-data-vq22301/macro-data/cpi_data.csv',
 's3://dsp-data-vq22301/macro-data/gdp_data.csv',
 's3://dsp-data-vq22301/macro-data/interest_rate_data.csv',
 's3://dsp-data-vq22301/macro-data/yield_10yr_data.csv',
 's3://dsp-data-vq22301/price_data2.csv']

In [24]:
inf = wr.s3.read_csv(path='s3://dsp-data-vq22301/macro-data/cpi_data.csv')
int_rate = wr.s3.read_csv(path='s3://dsp-data-vq22301/macro-data/interest_rate_data.csv')
gdp = wr.s3.read_csv(path='s3://dsp-data-vq22301/macro-data/gdp_data.csv')
bond = wr.s3.read_csv(path='s3://dsp-data-vq22301/macro-data/yield_10yr_data.csv')
# pc = wr.s3.read_csv(path='s3://dsp-data-vq22301/price_data2.csv')
# df = wr.s3.read_csv(path='s3://dsp-data-vq22301/all_data.csv')

Exception ignored in: <function _S3ObjectBase.__del__ at 0x7f3412e2d5a0>
Traceback (most recent call last):
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/awswrangler/s3/_fs.py", line 245, in __del__
    self.close()
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/awswrangler/s3/_fs.py", line 475, in close
    _utils.try_it(
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/awswrangler/_utils.py", line 810, in try_it
    return f(*args, **kwargs)
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/botocore/client.py", line 530, in _api_call
    return self._make_api_call(operation_name, kwargs)
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/botocore/client.py", line 947, in _make_api_call
    http, parsed_response = self._make_request(
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/botocore/client.py", line 970, in _make_request


In [25]:
import pandas as pd
import numpy as np

pd.set_option('display.max_rows', 1500)
pd.set_option('display.max_columns', 500)

Reading the data in

In [5]:
# df = pd.read_csv('./data/all_data.csv')
# df = df.sort_values(by=['TICKER', 'public_date'])

# Cleaning and Data Preparation

## Macro Data Cleaning

In [26]:
for econ_df in [int_rate, inf, gdp]:
    econ_df.DATE = pd.to_datetime(econ_df['DATE']) - pd.DateOffset(1)

In [27]:
bond.DATE = pd.to_datetime(bond.DATE)

### GDP

In [28]:
import warnings
warnings.filterwarnings('ignore')

gdp = gdp.set_index(pd.to_datetime(gdp['DATE'])).drop(columns='DATE')
gdp = gdp.resample('M').ffill().reset_index(drop=False)

def pct_change(x):
    return (x.loc[x.index.stop - 1] - x.loc[x.index.start]) / x.loc[x.index.start]

gdp['1yr_GDP'] = gdp['GDP'].rolling(13).apply(lambda x: pct_change(x))
gdp['1mo_GDP'] = gdp['GDP'].rolling(2).apply(lambda x: pct_change(x))

### Inflation

In [29]:
inf.columns

Index(['DATE', 'USACPIALLMINMEI'], dtype='object')

In [30]:
inf['1yr_inf_rate'] = inf['USACPIALLMINMEI'].rolling(13).apply(lambda x: pct_change(x))
inf['1mo_inf_rate'] = inf['USACPIALLMINMEI'].rolling(2).apply(lambda x: pct_change(x))

### 10-yr Treasury Yield

In [31]:
bond.loc[bond[bond['DGS10'] == '.'].index, 'DGS10'] = np.nan
bond = bond.fillna(method='ffill')
bond = bond.set_index('DATE').resample('D').ffill().reset_index()

In [32]:
wr.s3.list_objects('s3://dsp-data-vq22301')

['s3://dsp-data-vq22301/all_data.csv',
 's3://dsp-data-vq22301/all_data_pc_merged.csv',
 's3://dsp-data-vq22301/dataset_0-7575.csv',
 's3://dsp-data-vq22301/dataset_16294-end.csv',
 's3://dsp-data-vq22301/dataset_7576-16293.csv',
 's3://dsp-data-vq22301/dataset_drop_md.csv',
 's3://dsp-data-vq22301/final_dataset.csv',
 's3://dsp-data-vq22301/final_dataset_drop_target_na.csv',
 's3://dsp-data-vq22301/macro-data/cpi_data.csv',
 's3://dsp-data-vq22301/macro-data/gdp_data.csv',
 's3://dsp-data-vq22301/macro-data/interest_rate_data.csv',
 's3://dsp-data-vq22301/macro-data/yield_10yr_data.csv',
 's3://dsp-data-vq22301/price_data2.csv']

In [8]:
a = [[5,3,6,7,4], [3,2,4,6,3], [4,3,2,3,4], [3,2,1,2,1]]
import numpy as np

means = []
for j in range(len(a[0])):
    for k in range(len(a[0][0])):
        means.append(np.mean([a[i][j][k] for i in range(len(a))]))


In [9]:
means

[3.75, 2.5, 3.25, 4.5, 3.0]

In [7]:
np.mean([5, 3, 4, 3])

3.75

In [39]:
wr.s3.to_csv(df=gdp, path=f's3://dsp-data-vq22301/gdp_add_columns.csv')
wr.s3.to_csv(df=int_rate, path=f's3://dsp-data-vq22301/int_rate_add_columns.csv')
wr.s3.to_csv(df=inf, path=f's3://dsp-data-vq22301/inf_add_columns.csv')
wr.s3.to_csv(df=bond, path=f's3://dsp-data-vq22301/bond_add_columns.csv')

Exception ignored in: <function _S3ObjectBase.__del__ at 0x7f3412e2d5a0>
Traceback (most recent call last):
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/awswrangler/s3/_fs.py", line 245, in __del__
    self.close()
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/awswrangler/s3/_fs.py", line 475, in close
    _utils.try_it(
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/awswrangler/_utils.py", line 810, in try_it
    return f(*args, **kwargs)
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/botocore/client.py", line 530, in _api_call
    return self._make_api_call(operation_name, kwargs)
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/botocore/client.py", line 947, in _make_api_call
    http, parsed_response = self._make_request(
  File "/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/botocore/client.py", line 970, in _make_request


{'paths': ['s3://dsp-data-vq22301/bond_add_columns.csv'],
 'partitions_values': {}}

## Merging Dataframes

Merging the four dataframes (merging the economic data into the main financial dataframe).

In [10]:
df = df.drop(index=df[df['public_date'].isin([pd.to_datetime('2022-11-30'), pd.to_datetime('2022-12-31')])].index)
df.loc[:, 'public_date'] = pd.to_datetime(df['public_date'])

In [11]:
df.head()

gvkey  permno       adate       qdate          public_date   CAPEI     bm   
0   1000   25881  1969-12-31  1970-09-30  1971-01-31 00:00:00  10.950  0.427  \
1   1000   25881  1970-12-31  1970-12-31  1971-02-28 00:00:00  35.407  0.431   
2   1000   25881  1970-12-31  1970-12-31  1971-03-31 00:00:00  31.031  0.431   
3   1000   25881  1970-12-31  1970-12-31  1971-04-30 00:00:00  34.214  0.431   
4   1000   25881  1970-12-31  1971-03-31  1971-05-31 00:00:00  11.307  0.431   

     evm  pe_op_basic  pe_op_dil  pe_exi  pe_inc     ps     pcf  dpr    npm   
0  1.761          NaN        NaN  12.676  13.433  0.649  -3.254  0.0  0.060  \
1  7.010          NaN        NaN  19.866  65.441  0.652  24.411  0.0  0.041   
2  7.010          NaN        NaN  17.411  57.353  0.571  21.394  0.0  0.041   
3  7.010          NaN        NaN  19.196  63.235  0.630  23.588  0.0  0.041   
4  7.010          NaN        NaN  20.536  50.735  0.579  18.925  0.0  0.036   

   opmbd  opmad    gpm   ptpm    cfm    roa    roe   roce  efftax  aftret_eq   
0  0.133  0.105  0.326  0.101  0.077  0.287  0.287  0.341   0.515      0.211  \
1  0.119  0.089  0.327  0.080  0.071  0.173  0.181  0.189   0.481      0.181   
2  0.119  0.089  0.327  0.080  0.071  0.173  0.181  0.189   0.481      0.181   
3  0.119  0.089  0.327  0.080  0.071  0.173  0.181  0.189   0.481      0.181   
4  0.119  0.089  0.327  0.080  0.071  0.173  0.137  0.189   0.481      0.137   

   aftret_invcapx  aftret_equity  pretret_noa  pretret_earnat  GProf   
0           0.592          0.211        0.483           0.250  0.425  \
1           0.234          0.181        0.360           0.144  0.443   
2           0.234          0.181        0.360           0.144  0.443   
3           0.234          0.181        0.360           0.144  0.443   
4           0.083          0.137        0.360           0.144  0.443   

   equity_invcap  debt_invcap  totdebt_invcap  capital_ratio  int_debt   
0          0.876        0.124           0.742          0.124     0.368  \
1          0.920        0.080           1.160          0.080     0.723   
2          0.920        0.080           1.160          0.080     0.723   
3          0.920        0.080           1.160          0.080     0.723   
4          0.920        0.080           1.160          0.080     0.723   

   int_totdebt  cash_lt  invt_act  rect_act  debt_at  debt_ebitda  short_debt   
0        0.102    0.069     0.512     0.384    0.305        1.761       0.833  \
1        0.077    0.072     0.478     0.417    0.397        2.468       0.931   
2        0.077    0.072     0.478     0.417    0.397        2.468       0.931   
3        0.077    0.072     0.478     0.417    0.397        2.468       0.931   
4        0.077    0.072     0.478     0.417    0.397        2.468       0.931   

   curr_debt  lt_debt  profit_lct  ocf_lct  cash_debt  fcf_ocf  lt_ppent   
0      0.756    0.077       0.355   -0.525     -0.397      NaN     2.190  \
1      0.855    0.040       0.275    0.062      0.053   -1.287     2.581   
2      0.855    0.040       0.275    0.062      0.053   -1.287     2.581   
3      0.855    0.040       0.275    0.062      0.053   -1.287     2.581   
4      0.855    0.040       0.275    0.062      0.053   -1.287     2.581   

   dltt_be  debt_assets  debt_capital  de_ratio  intcov  intcov_ratio   
0    0.141        0.644         0.556     1.812   4.509         7.516  \
1    0.087        0.685         0.648     2.172   3.209         4.746   
2    0.087        0.685         0.648     2.172   3.209         4.746   
3    0.087        0.685         0.648     2.172   3.209         4.746   
4    0.087        0.685         0.648     2.172   3.209         4.746   

   cash_ratio  quick_ratio  curr_ratio  cash_conversion  inv_turn  at_turn   
0       0.091        0.604       1.238           70.634     5.220    2.159  \
1       0.085        0.569       1.090          115.766     3.202    1.459   
2       0.085        0.569       1.090          115.766     3.202    1.

In [29]:
df['public_date'] = df['public_date'].astype('datetime64[ns]')

In [96]:
df = df.drop(columns=[ 'FEDFUNDS', 'USACPIALLMINMEI', '1yr_inf_rate', '1mo_inf_rate', 'GDP',
       '1yr_GDP', '1mo_GDP', 'DGS10'])

In [97]:
for econ_df in [int_rate, inf, gdp, bond]:
    merged = df.merge(econ_df, how='left', left_on='public_date', right_on='DATE').drop(columns=['DATE'])
    df = merged

In [14]:
del int_rate
del inf
del gdp
del merged
del bond

In [100]:
df[['FEDFUNDS', 'USACPIALLMINMEI', '1yr_inf_rate', '1mo_inf_rate', 'GDP',
       '1yr_GDP', '1mo_GDP', 'DGS10']].isnull().sum()

FEDFUNDS           0
USACPIALLMINMEI    0
1yr_inf_rate       0
1mo_inf_rate       0
GDP                0
1yr_GDP            0
1mo_GDP            0
DGS10              0
dtype: int64

## Adding Target Variable and Pricing Info

In [228]:
# pc = pd.read_csv('./data/price_data2.csv')

There are some duplicate columns to be dropped.

In [15]:
pc.head()

permno PrimaryExch                              SecurityNm Ticker   
0   10000           Q  OPTIMUM MANUFACTURING INC; COM A; CONS  OMFGA  \
1   10000           Q  OPTIMUM MANUFACTURING INC; COM A; CONS  OMFGA   
2   10000           Q  OPTIMUM MANUFACTURING INC; COM A; CONS  OMFGA   
3   10000           Q  OPTIMUM MANUFACTURING INC; COM A; CONS  OMFGA   
4   10000           Q  OPTIMUM MANUFACTURING INC; COM A; CONS  OMFGA   

     MthCalDt  MthPrc    MthCap    MthVol  MthPrcVol  
0  1986-01-31  4.3750  16100.00  177082.0   634127.4  
1  1986-02-28  3.2500  11960.00   82800.0   319106.3  
2  1986-03-31  4.4375  16330.00  107801.0   445447.3  
3  1986-04-30  4.0000  15172.00   95700.0   399359.1  
4  1986-05-30  3.1094  11793.86  107362.0   402398.9

In [16]:
pc = pc.drop_duplicates()

In [17]:
len(df.TICKER.unique())

23282

In [18]:
len(pc.Ticker.unique())

23743

Dataframes are approximately same length, implying that most of the same tickers in df are also in pc.

We need to join on ticker, year, month. Therefore, we need to clean the date columns in each df so that even if days are different (they are in pc), the correct year/month lines pair up.

In [19]:
pc['MthCalDt'] = pd.to_datetime(pc['MthCalDt'])

pc['Year'] = pc["MthCalDt"].dt.year
pc['Month'] = pc["MthCalDt"].dt.month
df['Year'] = df['public_date'].dt.year
df['Month'] = df['public_date'].dt.month

Now we merge the df's and store the df to save computational time in the future.

In [20]:
len(pc)

3114455

In [21]:
merged = df.merge(pc, how='left', left_on=['permno', 'TICKER', 'Year', 'Month'], right_on=['permno', 'Ticker', 'Year', 'Month'])

In [23]:
len(merged)

2919528

In [24]:
wr.s3.to_csv(df=merged, path='s3://dsp-data-vq22301/all_data_pc_merged.csv')

{'paths': ['s3://dsp-data-vq22301/all_data_pc_merged.csv'],
 'partitions_values': {}}

In [6]:
merged = wr.s3.read_csv(path='s3://dsp-data-vq22301/all_data_pc_merged.csv')

/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/awswrangler/s3/_read_text_core.py:112: DtypeWarning: Columns (76) have mixed types. Specify dtype option on import or set low_memory=False.
  df: pd.DataFrame = parser_func(f, **pandas_kwargs)


There are 2.3% of lines which don't match. After investigation, it appears that the pricing dataset is missing information for about 70k ticker, year, month instances.

In [7]:
len(merged[merged.Ticker.isnull()]) / len(merged)

0.02414020348494688

In [27]:
# for i in merged[merged.ticker.isnull()].groupby('TICKER').count()['gvkey'].sort_values(ascending=False)

len(merged[merged.Ticker.isnull()])

70478

In [28]:
merged.MthPrc.isnull().sum()

65447

In [29]:
len(df[df.TICKER.isnull()])

39356

There is a large proportion of those where it is caused by no ticker in the original fundamental dataset. We should drop these.

In [8]:
merged = merged.drop(index=merged[merged.TICKER.isnull()].index)

In [9]:
len(merged[merged.Ticker.isnull()])

31122

# Adding the Target Variable

Next, we add our target variable: the 1yr return.

In [11]:
import warnings
warnings.filterwarnings('ignore')

import time

def diff_ret(x):
    try:
        return (x.iloc[0] - x.iloc[-1]) / x.iloc[-1]
    except:
        return np.nan

start=time.time()
    
for i, key in enumerate(merged.gvkey.unique()):
    if i % 100 == 0:
        print(i)
    temp = merged[merged['gvkey'] == key].copy()
    temp = temp.set_index(pd.to_datetime(temp['public_date']))
    sorted_idx = temp.index.sort_values(ascending=True)
    temp = temp.loc[sorted_idx].resample('M').asfreq()
    temp_rev = temp[::-1]
    temp_rev['1yr_return'] = np.nan
    temp_rev.loc[:, '1yr_return'] = temp_rev['MthPrc'].rolling(13).apply(diff_ret)
    temp = temp.join(temp_rev['1yr_return'])
    if i == 0:
        co_df = temp.reset_index(drop=True)
    else:
        temp.reset_index(drop=True)
        length = len(co_df)
        co_df = pd.concat([co_df, temp])
        co_df = co_df.reset_index(drop=True)
        end = time.time()
        if end - start > 12500:
            print(i)
            break

0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700


In [14]:
wr.s3.to_csv(df=co_df, path='s3://dsp-data-vq22301/dataset_16294-end.csv')

{'paths': ['s3://dsp-data-vq22301/dataset_16294-end.csv'],
 'partitions_values': {}}

In [15]:
wr.s3.list_objects("s3://dsp-data-vq22301")

['s3://dsp-data-vq22301/all_data.csv',
 's3://dsp-data-vq22301/all_data_pc_merged.csv',
 's3://dsp-data-vq22301/cpi_data.csv',
 's3://dsp-data-vq22301/dataset_0-7575.csv',
 's3://dsp-data-vq22301/dataset_16294-end.csv',
 's3://dsp-data-vq22301/dataset_7576-16293.csv',
 's3://dsp-data-vq22301/gdp_data.csv',
 's3://dsp-data-vq22301/interest_rate_data.csv',
 's3://dsp-data-vq22301/price_data2.csv']

In [18]:
df1 = wr.s3.read_csv('s3://dsp-data-vq22301/dataset_0-7575.csv')
df2 = wr.s3.read_csv('s3://dsp-data-vq22301/dataset_7576-16293.csv')
df3 = wr.s3.read_csv('s3://dsp-data-vq22301/dataset_16294-end.csv')

In [19]:
df = pd.concat([df1, df2, df3])

In [21]:
del df1
del df2
del df3

In [24]:
df.columns

Index(['Unnamed: 0.1', 'Unnamed: 0', 'gvkey', 'permno', 'adate', 'qdate',
       'public_date', 'CAPEI', 'bm', 'evm', 'pe_op_basic', 'pe_op_dil',
       'pe_exi', 'pe_inc', 'ps', 'pcf', 'dpr', 'npm', 'opmbd', 'opmad', 'gpm',
       'ptpm', 'cfm', 'roa', 'roe', 'roce', 'efftax', 'aftret_eq',
       'aftret_invcapx', 'aftret_equity', 'pretret_noa', 'pretret_earnat',
       'GProf', 'equity_invcap', 'debt_invcap', 'totdebt_invcap',
       'capital_ratio', 'int_debt', 'int_totdebt', 'cash_lt', 'invt_act',
       'rect_act', 'debt_at', 'debt_ebitda', 'short_debt', 'curr_debt',
       'lt_debt', 'profit_lct', 'ocf_lct', 'cash_debt', 'fcf_ocf', 'lt_ppent',
       'dltt_be', 'debt_assets', 'debt_capital', 'de_ratio', 'intcov',
       'intcov_ratio', 'cash_ratio', 'quick_ratio', 'curr_ratio',
       'cash_conversion', 'inv_turn', 'at_turn', 'rect_turn', 'pay_turn',
       'sale_invcap', 'sale_equity', 'sale_nwc', 'rd_sale', 'adv_sale',
       'staff_sale', 'accrual', 'ptb', 'PEG_trailing', 'div

In [25]:
df = df.drop(columns=['Unnamed: 0.1', 'Unnamed: 0'])

In [27]:
df = df.dropna(axis = 0, how = 'all')

In [34]:
wr.s3.to_csv(df=df, path='s3://dsp-data-vq22301/final_dataset.csv')

{'paths': ['s3://dsp-data-vq22301/final_dataset.csv'], 'partitions_values': {}}

# Dropping data with no targe variable values

In [5]:
df = wr.s3.read_csv('s3://dsp-data-vq22301/final_dataset.csv')

/home/ec2-user/anaconda3/envs/python3/lib/python3.10/site-packages/awswrangler/s3/_read_text_core.py:112: DtypeWarning: Columns (76) have mixed types. Specify dtype option on import or set low_memory=False.
  df: pd.DataFrame = parser_func(f, **pandas_kwargs)


In [6]:
len(df)

2880172

In [7]:
import random

while True:
    i = random.randint(0, len(df) - 500)
    display(df.iloc[i:i+500, :])
    wait = input("Press enter to continue...")

Unnamed: 0     gvkey   permno       adate       qdate public_date   
2811987      498941  176899.0  16448.0  2019-12-31  2020-06-30  2020-09-30  \
2811988      498942  176899.0  16448.0  2019-12-31  2020-06-30  2020-10-31   
2811989      498943  176899.0  16448.0  2019-12-31  2020-09-30  2020-11-30   
2811990      498944  176899.0  16448.0  2019-12-31  2020-09-30  2020-12-31   
2811991      498945  176899.0  16448.0  2019-12-31  2020-09-30  2021-01-31   
2811992      498946  176899.0  16448.0  2020-12-31  2020-12-31  2021-02-28   
2811993      498947  176899.0  16448.0  2020-12-31  2020-12-31  2021-03-31   
2811994      498948  176899.0  16448.0  2020-12-31  2020-12-31  2021-04-30   
2811995      498949  176899.0  16448.0  2020-12-31  2021-03-31  2021-05-31   
2811996      498950  176899.0  16448.0  2020-12-31  2021-03-31  2021-06-30   
2811997      498951  176899.0  16448.0  2020-12-31  2021-03-31  2021-07-31   
2811998      498952  176899.0  16448.0  2020-12-31  2021-06-30  2021-08-31   
2811999      498953  176899.0  16448.0  2020-12-31  2021-06-30  2021-09-30   
2812000      498954  176899.0  16448.0  2020-12-31  2021-06-30  2021-10-31   
2812001      498955  176899.0  16448.0  2020-12-31  2021-09-30  2021-11-30   
2812002      498956  176899.0  16448.0  2020-12-31  2021-09-30  2021-12-31   
2812003      498957  176899.0  16448.0  2020-12-31  2021-09-30  2022-01-31   
2812004      498958  176899.0  16448.0  2021-12-31  2021-12-31  2022-02-28   
2812005      498959  176899.0  16448.0  2021-12-31  2021-12-31  2022-03-31   
2812006      498960  176899.0  16448.0  2021-12-31  2021-12-31  2022-04-30   
2812007      498961  176899.0  16448.0  2021-12-31  2022-03-31  2022-05-31   
2812008      498962  176899.0  16448.0  2021-12-31  2022-03-31  2022-06-30   
2812009      498963  176899.0  16448.0  2021-12-31  2022-03-31  2022-07-31   
2812010      498964  176899.0  16448.0  2021-12-31  2022-06-30  2022-08-31   
2812011      498965  176899.0  16448.0  2021-12-31  2022-06-30  2022-09-30   
2812012      498966  176899.0  16448.0  2021-12-31  2022-06-30  2022-10-31   
2812013      498967  176899.0  16448.0  2021-12-31  2022-09-30  2022-11-30   
2812014      498968  176899.0  16448.0  2021-12-31  2022-09-30  2022-12-31   
2812015      498969  176920.0  91936.0  2007-03-31  2007-06-30  2007-08-31   
2812016      498970  176920.0  91936.0  2007-03-31  2007-06-30  2007-09-30   
2812017      498971  176920.0  91936.0  2007-03-31  2007-06-30  2007-10-31   
2812018      498972  176920.0  91936.0  2007-03-31  2007-09-30  2007-11-30   
2812019      498973  176920.0  91936.0  2007-03-31  2007-09-30  2007-12-31   
2812020      498974  176920.0  91936.0  2007-03-31  2007-09-30  2008-01-31   
2812021      498975  176920.0  91936.0  2007-03-31  2007-12-31  2008-02-29   
2812022      498976  176920.0  91936.0  2007-03-31  2007-12-31  2008-03-31   
2812023      498977  176920.0  91936.0  2007-03-31  2007-12-31  2008-04-30   
2812024      498978  176920.0  91936.0  2008-03-31  2008-03-31  2008-05-31   
2812025      498979  176920.0  91936.0  2008-03-31  2008-03-31  2008-06-30   
2812026      498980  176920.0  91936.0  2008-03-31  2008-03-31  2008-07-31   
2812027      498981  176920.0  91936.0  2008-03-31  2008-06-30  2008-08-31   
2812028      498982  176920.0  91936.0  2008-03-31  2008-06-30  2008-09-30   
2812029      498983  176920.0  91936.0  2008-03-31  2008-06-30  2008-10-31   
2812030      498984  176920.0  91936.0  2008-03-31  2008-09-30  2008-11-30   
2812031      498985  176920.0  91936.0  2008-03-31  2008-09-30  2008-12-31   
2812032      498986  176920.0  91936.0  2008-03-31  2008-09-30  2009-01-31   
2812033      498987  176920.0  91936.0  2008-03-31  2008-12-31  2009-02-28   
2812034      498988  176920.0  91936.0  2008-03-31  2008-12-31  2009-03-31   
2812035      498989  176920.0  91936.0  2008-03-31  2008-12-31  2009-04-30   
2812036      498990  176920.0  91936.0         NaN  2008-12-31  2009-05-31   
2812037      498991  176928.0  

Press enter to continue...


Unnamed: 0    gvkey   permno       adate       qdate public_date   
2520876      202812  65850.0  85539.0  2012-12-31  2013-03-31  2013-05-31  \
2520877      202813  65850.0  85539.0  2012-12-31  2013-03-31  2013-06-30   
2520878      202814  65850.0  85539.0  2012-12-31  2013-03-31  2013-07-31   
2520879      202815  65850.0  85539.0  2012-12-31  2013-06-30  2013-08-31   
2520880      202816  65850.0  85539.0  2012-12-31  2013-06-30  2013-09-30   
2520881      202817  65850.0  85539.0  2012-12-31  2013-06-30  2013-10-31   
2520882      202818  65850.0  85539.0  2012-12-31  2013-09-30  2013-11-30   
2520883      202819  65850.0  85539.0  2012-12-31  2013-09-30  2013-12-31   
2520884      202820  65850.0  85539.0  2012-12-31  2013-09-30  2014-01-31   
2520885      202821  65850.0  85539.0  2013-12-31  2013-12-31  2014-02-28   
2520886      202822  65850.0  85539.0  2013-12-31  2013-12-31  2014-03-31   
2520887      202823  65850.0  85539.0  2013-12-31  2013-12-31  2014-04-30   
2520888      202824  65850.0  85539.0  2013-12-31  2014-03-31  2014-05-31   
2520889      202825  65850.0  85539.0  2013-12-31  2014-03-31  2014-06-30   
2520890      202826  65850.0  85539.0  2013-12-31  2014-03-31  2014-07-31   
2520891      202827  65850.0  85539.0  2013-12-31  2014-06-30  2014-08-31   
2520892      202828  65850.0  85539.0  2013-12-31  2014-06-30  2014-09-30   
2520893      202829  65850.0  85539.0  2013-12-31  2014-06-30  2014-10-31   
2520894      202830  65850.0  85539.0  2013-12-31  2014-09-30  2014-11-30   
2520895      202831  65850.0  85539.0  2013-12-31  2014-09-30  2014-12-31   
2520896      202832  65850.0  85539.0  2013-12-31  2014-09-30  2015-01-31   
2520897      202833  65850.0  85539.0  2014-12-31  2014-12-31  2015-02-28   
2520898      202834  65850.0  85539.0  2014-12-31  2014-12-31  2015-03-31   
2520899      202835  65850.0  85539.0  2014-12-31  2014-12-31  2015-04-30   
2520900      202836  65850.0  85539.0  2014-12-31  2015-03-31  2015-05-31   
2520901      202837  65850.0  85539.0  2014-12-31  2015-03-31  2015-06-30   
2520902      202838  65850.0  85539.0  2014-12-31  2015-03-31  2015-07-31   
2520903      202839  65850.0  85539.0  2014-12-31  2015-06-30  2015-08-31   
2520904      202840  65850.0  85539.0  2014-12-31  2015-06-30  2015-09-30   
2520905      202841  65850.0  85539.0  2014-12-31  2015-06-30  2015-10-31   
2520906      202842  65850.0  85539.0  2014-12-31  2015-09-30  2015-11-30   
2520907      202843  65850.0  85539.0  2014-12-31  2015-09-30  2015-12-31   
2520908      202844  65850.0  85539.0  2014-12-31  2015-09-30  2016-01-31   
2520909      202845  65850.0  85539.0  2015-12-31  2015-12-31  2016-02-29   
2520910      202846  65850.0  85539.0  2015-12-31  2015-12-31  2016-03-31   
2520911      202847  65850.0  85539.0  2015-12-31  2015-12-31  2016-04-30   
2520912      202848  65850.0  85539.0  2015-12-31  2016-03-31  2016-05-31   
2520913      202849  65850.0  85539.0  2015-12-31  2016-03-31  2016-06-30   
2520914      202850  65850.0  85539.0  2015-12-31  2016-03-31  2016-07-31   
2520915      202851  65850.0  85539.0  2015-12-31  2016-06-30  2016-08-31   
2520916      202852  65850.0  85539.0  2015-12-31  2016-06-30  2016-09-30   
2520917      202853  65850.0  85539.0  2015-12-31  2016-06-30  2016-10-31   
2520918      202854  65850.0  85539.0  2015-12-31  2016-09-30  2016-11-30   
2520919      202855  65850.0  85539.0  2015-12-31  2016-09-30  2016-12-31   
2520920      202856  65850.0  85539.0  2015-12-31  2016-09-30  2017-01-31   
2520921      202857  65850.0  85539.0  2016-12-31  2016-12-31  2017-02-28   
2520922      202858  65850.0  85539.0  2016-12-31  2016-12-31  2017-03-31   
2520923      202859  65850.0  85539.0  2016-12-31  2016-12-31  2017-04-30   
2520924      202860  65850.0  85539.0  2016-12-31  2017-03-31  2017-05-31   
2520925      202861  65850.0  85539.0  2016-12-31  2017-03-31  2017-06-30   
2520926      202862  65850.0  85539.0  2016-12-31  2017-03-31  2017-07-31   
25209

KeyboardInterrupt: Interrupted by user

In [16]:
df2 = df.drop(index=df[df['1yr_return'].isnull()].index)

In [20]:
wr.s3.to_csv(df=df2, path='s3://dsp-data-vq22301/final_dataset_drop_target_na.csv')

{'paths': ['s3://dsp-data-vq22301/final_dataset_drop_target_na.csv'],
 'partitions_values': {}}